In [1]:
import pandas as pd
import numpy as np
from tqdm import tqdm
from geopy.geocoders import Nominatim
import plotly.graph_objects as go
import plotly.express as px
from math import radians, cos, sin, asin, sqrt
from itertools import islice

#### Loading the dataset

In [2]:
business = pd.read_json('/Users/prajwalkhot/Documents/IDS/Project/Yelp/yelp_dataset/Business.json', lines= True)
business = business.dropna()
business.reset_index(drop= True, inplace= True)

In [3]:
business

business_id                                 name  \
0       6iYb2HFDywm3zjuRg0shjw                  Oskar Blues Taproom   
1       tCbdrRPZA0oiIYSmHG3J0w              Flying Elephants at PDX   
2       bvN78flM8NLprQ1a1y5dRg                       The Reclaimory   
3       PE9uqAjdw0E4-8mjGl3wVA                    Crossfit Terminus   
4       D4JtQNTI4X3KcbzacDJsMw                  Bob Likes Thai Food   
...                        ...                                  ...   
123174  rCTPX2ehHPFnHTe0aK9ZPQ        JDM Toyota & Honda Specialist   
123175  d6iEdtgLKelWKtb-2UmE2A  Master Finish Mobile Auto Detailing   
123176  bQX-kwVTyZgcdZGEPzce6Q                         Webb's Honey   
123177  wvFZ06nmPmQ2-IVoPqVYLA                Painting with a Twist   
123178  ngmLL5Y5OT-bYHKU0kKrYA                          Zora Grille   

                     address               city state postal_code   latitude  \
0               921 Pearl St            Boulder    CO       80302  40.017544   
1        7000 NE Airport Way           Portland    OR       97218  45.588906   
2         4720 Hawthorne Ave           Portland    OR       97214  45.511907   
3        1046 Memorial Dr SE            Atlanta    GA       30316  33.747027   
4               3755 Main St          Vancouver    BC         V5V  49.251342   
...                      ...                ...   ...         ...        ...   
123174    6629 E Colonial Dr            Orlando    FL       32807  28.566161   
123175      29 Greenwood Ave            Needham    MA       02492  42.282399   
123176    21777 State Rd 520            Orlando    FL       32833  28.499836   
123177  2164 S Chickasaw Trl            Orlando    FL       32825  28.511615   
123178   1370 E Altamonte Dr  Altamonte Springs    FL       32701  28.663047   

         longitude  stars  review_count  is_open  \
0      -105.283348    4.0            86        1   
1      -122.593331    4.0           126        1   
2      -122.613693    4.5            13        1   
3       -84.353424    4.0            14        1   
4      -123.101333    3.5           169        1   
...            ...    ...           ...      ...   
123174  -81.298123    4.5             8        1   
123175  -71.225169    1.0            11        1   
123176  -81.047478    4.5            18        1   
123177  -81.270020    5.0             8        0   
123178  -81.346728    4.5            82        0   

                                               attributes  \
0       {'RestaurantsTableService': 'True', 'WiFi': 'u...   
1       {'RestaurantsTakeOut': 'True', 'RestaurantsAtt...   
2       {'BusinessAcceptsCreditCards': 'True', 'Restau...   
3       {'GoodForKids': 'False', 'BusinessParking': '{...   
4       {'GoodForKids': 'True', 'Alcohol': 'u'none'', ...   
...                                                   ...   
123174             {'BusinessAcceptsCreditCards': 'True'}   
123175             {'BusinessAcceptsCreditCards': 'True'}   
123176  {'RestaurantsTakeOut': 'True', 'RestaurantsPri...   
123177  {'DogsAllowed': 'False', 'ByAppointmentOnly': ...   
123178  {'RestaurantsReservations': 'True', 'OutdoorSe...   

                                               categories  \
0       Gastropubs, Food, Beer Gardens, Restaurants, B...   
1       Salad, Soup, Sandwiches, Delis, Restaurants, C...   
2       Antiques, Fashion, Used, Vintage & Consignment...   
3       Gyms, Active Life, Interval Training Gyms, Fit...   
4                                       Restaurants, Thai   
...                                                   ...   
123174             Automotive, Tires, Towing, Auto Repair   
123175                         Automotive, Auto Detailing   
123176      Health Markets, Food, Specialty Food, Grocery   
123177  Arts & Entertainment, Paint & Sip, Art Classes...   
123178  Restaurants, Middle Eastern, Mediterranean, Pe...   

                                                    hours  
0       {'Monday': '11:0-23:0', 'Tuesday': '11:0-23:0'

#### Value count for the column categories

In [10]:
business['categories'].value_counts()

Pizza, Restaurants                                                                    524
Restaurants, Pizza                                                                    505
Restaurants, Chinese                                                                  385
Mexican, Restaurants                                                                  380
Chinese, Restaurants                                                                  377
                                                                                     ... 
Food, Sandwiches, Bakeries, Restaurants, Empanadas, Delis, Puerto Rican, Caribbean      1
American (New), Nightlife, Restaurants, Bars, American (Traditional)                    1
Cocktail Bars, Bars, Restaurants, Nightlife, Tapas/Small Plates, Beer Bar               1
Bars, Nightlife, Pizza, Italian, Restaurants                                            1
Restaurants, Seafood, Greek, Mediterranean, Sandwiches                                  1
Name: cate

#### Creating a dictionary to store the type of restaurant and the total number of that kind in the United States

In [20]:
cats_raw = {}
for i in tqdm(range(len(business))):
    for j in business['categories'][i].split(','):
        temp = j.replace(" ", "")
        if temp in cats_raw:
            cats_raw[temp] += 1
        else:
            cats_raw[temp] = 1
cats_raw

100%|██████████| 42646/42646 [00:00<00:00, 137276.06it/s]


{'Bagels': 507,
 'Food': 14455,
 'Sandwiches': 6505,
 'Breakfast&Brunch': 5148,
 'Coffee&Tea': 4009,
 'Restaurants': 42646,
 'Cupcakes': 81,
 'Vegan': 1117,
 'CustomCakes': 75,
 'American(Traditional)': 5886,
 'Pancakes': 20,
 'Burgers': 3969,
 'FoodDeliveryServices': 718,
 'EventPlanning&Services': 2415,
 'Caterers': 1629,
 'SpecialtyFood': 1824,
 'Pizza': 4907,
 'FoodTrucks': 1741,
 'Salad': 2537,
 'Cafes': 2582,
 'Creperies': 185,
 'IceCream&FrozenYogurt': 887,
 'JuiceBars&Smoothies': 923,
 'Waffles': 195,
 'Desserts': 1766,
 'Nightlife': 7879,
 'Bars': 7553,
 'American(New)': 4956,
 'ActiveLife': 291,
 'Bowling': 56,
 'Bakeries': 1763,
 'Poke': 190,
 'AsianFusion': 1776,
 'ComfortFood': 676,
 'Delis': 1650,
 'Italian': 3134,
 'Thai': 1162,
 'Korean': 696,
 'ChickenShop': 443,
 'ChickenWings': 1996,
 'FastFood': 4717,
 'Indian': 944,
 'Caribbean': 586,
 'ConvenienceStores': 229,
 'Pop-UpRestaurants': 53,
 'PoolHalls': 87,
 'Chinese': 2913,
 'Seafood': 2694,
 'Vietnamese': 980,
 'Pak

In [24]:
cats_raw_list = sorted(cats_raw.items(), key=lambda x: x[1], reverse=True)
cats_raw_list = cats_raw_list[1:]
x_val, y_val = zip(*cats_raw_list) 

fig = go.Figure()
fig.add_trace(
    go.Bar(x = x_val[:25], y = y_val[:25])
)

fig.update_layout(
    yaxis_title = "Number of Restaurants",
    xaxis_title = "Type of Restaurant"
)

fig.show()

#### Sorting the dataframe by city name

In [25]:
business = business.sort_values(by=['city'])
business.reset_index(drop= True, inplace= True)
business

business_id                 name  is_open  stars  \
0      SjrWj9ZzDEmnAFwUD-ekMA  Emerald City Bagels        1    4.0   
1      8ZO7i1rJAsp19D-DXOvPAg         Hebrew Bakes        1    4.5   
2      Mn7iwfUnmTcDOFm0z8eOLA                 IHOP        1    2.0   
3      -H_cbWJ6Wqe5lxRm4l7h_w          Spread & Co        1    4.5   
4      _njeaLgMzbaVT5VGUb_YTg             40 North        1    4.5   
...                       ...                  ...      ...    ...   
42641  KGxQIqbHO-dfsXjtjdXyEg   Enzo's on the Lake        1    4.5   
42642  aw8kSAZLGJgxykRpp8HRcQ  Mr. and Mrs. Pickle        0    4.5   
42643  WlZXHllnY8rrEEXXZpsiaw          Steak Shack        0    4.5   
42644  K5bWNbVGGXAOp3VCdA59lQ    Uno Chicago Grill        0    2.0   
42645  9pRrhkIAIA-DnAVz6OwDCQ      Full Belly Fare        1    5.0   

       review_count                                         categories  \
0               198  Bagels, Food, Sandwiches, Breakfast & Brunch, ...   
1                11   Restaurants, Food, Cupcakes, Vegan, Custom Cakes   
2                50  Food, Breakfast & Brunch, American (Traditiona...   
3                61  Food, Food Delivery Services, Restaurants, Eve...   
4               220  Pizza, Restaurants, Food Trucks, Food, Sandwic...   
...             ...                                                ...   
42641           148  Event Planning & Services, Venues & Event Spac...   
42642            10  Delis, Restaurants, Specialty Food, Local Flav...   
42643            17  Food Stands, Food Trucks, Restaurants, Food, F...   
42644            24  American (Traditional), Restaurants, Pizza, Gl...   
42645            12  Food Delivery Services, Food, Specialty Food, ...   

                                              attributes state       city  \
0      {'GoodForMeal': '{'dessert': False, 'latenight...    GA    ATLANTA   
1      {'BikeParking': 'True', 'RestaurantsTakeOut': ...    GA    ATLANTA   
2      {'BusinessAcceptsCreditCards': 'True', 'CoatCh...    TX     AUSTIN   
3      {'Caters': 'True', 'RestaurantsPriceRange2': '...    TX     AUSTIN   
4      {'RestaurantsTakeOut': 'True', 'RestaurantsDel...    TX     AUSTIN   
...                                                  ...   ...        ...   
42641  {'RestaurantsAttire': 'u'dressy'', 'NoiseLevel...    FL   longwood   
42642  {'BusinessAcceptsCreditCards': 'True', 'Busine...    FL   longwood   
42643  {'OutdoorSeating': 'True', 'RestaurantsAttire'...    OR  milwaukie   
42644  {'BusinessAcceptsCreditCards': 'True', 'Busine...    MA     newton   
42645  {'RestaurantsPriceRange2': '2', 'BusinessAccep...    OR   portland   

        latitude   longitude  
0      33.739961  -84.346463  
1      33.738497  -84.416651  
2      30.206563  -97.975722  
3      30.308698  -97.750456  
4      30.274976  -97.751705  
...          ...         ...  
42641  28.690442  -81.329239  
42642  28.683497  -81.351564  
42643  45.443336 -122.642012  
42644  42.357291  -71.185248  
42645  45.558962 -122.661814  

[42646 rows x 11 columns]

#### Selecting Restaurant businesses only

In [26]:
business = business[business['categories'].astype(str).str.contains('Restaurants')]
business.reset_index(drop= True, inplace= True)
business

business_id                 name  is_open  stars  \
0      SjrWj9ZzDEmnAFwUD-ekMA  Emerald City Bagels        1    4.0   
1      8ZO7i1rJAsp19D-DXOvPAg         Hebrew Bakes        1    4.5   
2      Mn7iwfUnmTcDOFm0z8eOLA                 IHOP        1    2.0   
3      -H_cbWJ6Wqe5lxRm4l7h_w          Spread & Co        1    4.5   
4      _njeaLgMzbaVT5VGUb_YTg             40 North        1    4.5   
...                       ...                  ...      ...    ...   
42641  KGxQIqbHO-dfsXjtjdXyEg   Enzo's on the Lake        1    4.5   
42642  aw8kSAZLGJgxykRpp8HRcQ  Mr. and Mrs. Pickle        0    4.5   
42643  WlZXHllnY8rrEEXXZpsiaw          Steak Shack        0    4.5   
42644  K5bWNbVGGXAOp3VCdA59lQ    Uno Chicago Grill        0    2.0   
42645  9pRrhkIAIA-DnAVz6OwDCQ      Full Belly Fare        1    5.0   

       review_count                                         categories  \
0               198  Bagels, Food, Sandwiches, Breakfast & Brunch, ...   
1                11   Restaurants, Food, Cupcakes, Vegan, Custom Cakes   
2                50  Food, Breakfast & Brunch, American (Traditiona...   
3                61  Food, Food Delivery Services, Restaurants, Eve...   
4               220  Pizza, Restaurants, Food Trucks, Food, Sandwic...   
...             ...                                                ...   
42641           148  Event Planning & Services, Venues & Event Spac...   
42642            10  Delis, Restaurants, Specialty Food, Local Flav...   
42643            17  Food Stands, Food Trucks, Restaurants, Food, F...   
42644            24  American (Traditional), Restaurants, Pizza, Gl...   
42645            12  Food Delivery Services, Food, Specialty Food, ...   

                                              attributes state       city  \
0      {'GoodForMeal': '{'dessert': False, 'latenight...    GA    ATLANTA   
1      {'BikeParking': 'True', 'RestaurantsTakeOut': ...    GA    ATLANTA   
2      {'BusinessAcceptsCreditCards': 'True', 'CoatCh...    TX     AUSTIN   
3      {'Caters': 'True', 'RestaurantsPriceRange2': '...    TX     AUSTIN   
4      {'RestaurantsTakeOut': 'True', 'RestaurantsDel...    TX     AUSTIN   
...                                                  ...   ...        ...   
42641  {'RestaurantsAttire': 'u'dressy'', 'NoiseLevel...    FL   longwood   
42642  {'BusinessAcceptsCreditCards': 'True', 'Busine...    FL   longwood   
42643  {'OutdoorSeating': 'True', 'RestaurantsAttire'...    OR  milwaukie   
42644  {'BusinessAcceptsCreditCards': 'True', 'Busine...    MA     newton   
42645  {'RestaurantsPriceRange2': '2', 'BusinessAccep...    OR   portland   

        latitude   longitude  
0      33.739961  -84.346463  
1      33.738497  -84.416651  
2      30.206563  -97.975722  
3      30.308698  -97.750456  
4      30.274976  -97.751705  
...          ...         ...  
42641  28.690442  -81.329239  
42642  28.683497  -81.351564  
42643  45.443336 -122.642012  
42644  42.357291  -71.185248  
42645  45.558962 -122.661814  

[42646 rows x 11 columns]

#### Considering states with at least 500+ Restaurants registered with Yelp

In [27]:
states = dict(business['state'].value_counts()[:9])
states

{'MA': 8676,
 'FL': 6601,
 'OR': 6319,
 'BC': 6092,
 'GA': 5161,
 'TX': 4629,
 'OH': 3774,
 'CO': 730,
 'WA': 657}

#### A new dataframe for the above mentioned states

In [29]:
for k in states:
    globals()['%s' % k] = business[business['state'] == k]
rest_df = pd.concat([MA, FL, OR, BC, GA, TX, OH, CO, WA], ignore_index=True)
rest_df

business_id                     name  is_open  stars  \
0      o-GSqiYjfHp_2rPGuqJfKQ       The Big A Pizzeria        0    2.5   
1      vFxYhoBFbnQkPXKYN782bg               S & I Thai        1    4.0   
2      QkWj_XXTdB9Qf0k7i4F2AQ                    Bibim        0    3.5   
3      zFTHp5PEeVMlNzvBL0lzHg                      KFC        1    2.0   
4      dRWndf4b9W0LqmPEX7hlxg            KTown Chicken        1    3.0   
...                       ...                      ...      ...    ...   
42634  EmoECrrncV5CYViTSchSZg  Sunrise Bagels and More        0    3.5   
42635  JkhXi-3RJtmUTlkjrSdWSw   Thai Orchid Restaurant        1    4.0   
42636  63fTpDb6IhHW-z9he0BCrg               China Cook        1    3.5   
42637  elVQnVHyBz4mN_QeGyQQeA                 Pita Pit        0    3.5   
42638  1Rsw9ZAky8djRMUHuya7_Q               Ginger Pop        1    3.5   

       review_count                                         categories  \
0                77                          Delis, Pizza, Restaurants   
1               482                                  Thai, Restaurants   
2               143                                Korean, Restaurants   
3                60  Chicken Shop, Chicken Wings, Restaurants, Fast...   
4                61                 Korean, Restaurants, Chicken Wings   
...             ...                                                ...   
42634            65  Food, Bagels, Restaurants, Breakfast & Brunch,...   
42635           636     Restaurants, Nightlife, Thai, Sushi Bars, Bars   
42636            92                               Restaurants, Chinese   
42637            27  Restaurants, Sandwiches, Mexican, Mediterranea...   
42638           281  Nightlife, Thai, Wine Bars, Restaurants, Cockt...   

                                              attributes state       city  \
0      {'RestaurantsPriceRange2': '1', 'Caters': 'Fal...    MA    Allston   
1      {'BusinessAcceptsCreditCards': 'True', 'Restau...    MA    Allston   
2      {'BusinessParking': '{'garage': False, 'street...    MA    Allston   
3      {'BusinessParking': '{'garage': False, 'street...    MA    Allston   
4      {'GoodForMeal': '{'dessert': False, 'latenight...    MA    Allston   
...                                                  ...   ...        ...   
42634  {'BusinessAcceptsCreditCards': 'True', 'Busine...    WA  Vancouver   
42635  {'RestaurantsTakeOut': 'True', 'Caters': 'True...    WA  Vancouver   
42636  {'GoodForKids': 'True', 'RestaurantsGoodForGro...    WA  Vancouver   
42637  {'RestaurantsDelivery': 'True', 'RestaurantsAt...    WA  Vancouver   
42638  {'BusinessAcceptsCreditCards': 'True', 'Outdoo...    WA  Vancouver   

        latitude   longitude  
0      42.352296  -71.140500  
1      42.352930  -71.132944  
2      42.351485  -71.131519  
3      42.353585  -71.138933  
4      42.352165  -71.131591  
...          ...         ...  
42634  45.627829 -122.679520  
42635  45.629520 -122.672825  
42636  45.641867 -122.648043  
42637  45.609279 -122.502620  
42638  45.619157 -122.644590  

[42639 rows x 11 columns]

In [30]:
fig = px.scatter_mapbox(rest_df, lat="latitude", lon="longitude", hover_name="name", hover_data=["city"], zoom=3, height=300)
fig.update_layout(mapbox_style="open-street-map")
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.update_layout(
    width=1000,
    height=600,
)

fig.show()

------------------------------------------------------------------------------------------------------------------

#### Finding distance between 2 locations

In [31]:
from math import radians, cos, sin, asin, sqrt
# Calculate the great circle distance between two points on the earth
def dist(lat1, long1, lat2, long2):
    #One of lat and long can be user's location
    # convert decimal degrees to radians 
    lat1, long1, lat2, long2 = map(radians, [lat1, long1, lat2, long2])
    # haversine formula 
    dlon = long2 - long1 
    dlat = lat2 - lat1 
    a = sin(dlat/2)**2 + cos(lat1) * cos(lat2) * sin(dlon/2)**2
    c = 2 * asin(sqrt(a)) 
    # Radius of earth in kilometers is 6371
    km = 6371* c
    return km

def find_nearest(rest, lat, long):
    distances = rest.apply(
        lambda row: dist(lat, long, row['latitude'], row['longitude']), 
        axis=1)
    return rest.loc[distances.idxmin(), 'name']


#### Created a dummy members' dataframe to store their name and location

In [165]:
members = {'Username': ["Sharanya", "Anjani", "Priyanka", "Samruddhi"], 'lat': [42.534248, 49.660160, 42.633425, 46.122195], 'lon': [-70.813648, -122.586133, -71.316172, -122.578420]}
members= pd.DataFrame(data=members)
members

Username        lat         lon
0   Sharanya  42.534248  -70.813648
1     Anjani  49.660160 -122.586133
2   Priyanka  42.633425  -71.316172
3  Samruddhi  46.122195 -122.578420

#### Taking user input for their name, address and type of restaurant they want to visit

In [168]:
name = input("Enter your name:")
loc = input("Enter your address:")
rest_category = input("Enter cuisine:")

#making an instance of Nominatim class
geolocator = Nominatim(user_agent="my_request")

#applying geocode method to get the location
location = geolocator.geocode(loc)

#printing address and coordinates
print(location.address)
print((location.latitude, location.longitude))
new_row = {"Username": name, "lat": location.latitude, "lon": location.longitude}
members = members.append(new_row, ignore_index = True)

Enter your name:Prajwal
Enter your address:Boston Uni
Enter cuisine:Bars
Boston University, Manchester Road, Coolidge Corner, Boston, Norfolk County, Massachusetts, 02215, United States
(42.35031725, -71.10122725124097)


In [169]:
members['name'] = members.apply(lambda row: find_nearest(business.query('categories.str.contains("'+ rest_category + '")', engine='python'), row['lat'], row['lon']), axis=1)


In [170]:
members_new = pd.merge(members,business[['name','latitude','longitude', 'stars']],on='name', how='left')
members_new=members_new.rename(columns = {'lat':'m_lat','lon':'m_lon','latitude':'h_lat','longitude':'h_lon'})
members_new

Username      m_lat       m_lon                     name      h_lat  \
0   Sharanya  42.534248  -70.813648  The Barnacle Restaurant  42.506941   
1     Anjani  49.660160 -122.586133             Hiraku Sushi  49.292803   
2   Priyanka  42.633425  -71.316172             WU Loon Ming  42.584469   
3  Samruddhi  46.122195 -122.578420   Mahoney's Public House  45.698985   
4    Prajwal  42.350317  -71.101227            Basho Express  42.349341   
5    Prajwal  42.350317  -71.101227            Basho Express  42.349341   

        h_lon  stars  
0  -70.844396    3.5  
1 -122.755610    3.5  
2  -71.293401    2.5  
3 -122.703598    4.5  
4  -71.103982    3.0  
5  -71.103982    3.0

#### Plotting the members and the nearest restaurant on the map

In [171]:
mapbox_access_token = 'pk.eyJ1IjoicHJhandhbGtob3QxNCIsImEiOiJja3d1NHQzeDkxbW9qMm5qdmVzaDloMWNhIn0.CFF-9llt4RnfRomF64MDcg'

fig = go.Figure()

fig.add_trace(go.Scattermapbox(
        lat=members_new['m_lat'],
        lon=members_new['m_lon'],
        mode='markers',
        marker=go.scattermapbox.Marker(
            size=10,
            color='rgb(255, 0, 0)',
            opacity=0.7
        ),
        text=members_new['Username'],
        hoverinfo='text'
    ))

fig.add_trace(go.Scattermapbox(
        lat=members_new['h_lat'],
        lon=members_new['h_lon'],
        mode='markers',
        marker = {'size': 10, 'symbol' : 'restaurant', 'color':'rgb(0, 0, 255)'},
        text = members_new['name'],
        hoverinfo='text'
    ))

fig.update_layout(
    title='Map',
    autosize=True,
    hovermode='closest',
    showlegend=False,
    mapbox=dict(
        accesstoken=mapbox_access_token,
        bearing=0,
        center=dict(
            lat=38,
            lon=-94
        ),
        pitch=0,
        zoom=3,
        style='light'
    ),
)

fig.show()


_________________

In [172]:
remove_list = ['Beer', 
               'Chiropractors', 
               'WaterHeaterInstallation/Repair', 
               'AmusementParks', 
               'Food', 
               'Restaurants', 
               'Antiques', 
               'Fashion', 
               'Used', 
               'Shopping', 
               'FurnitureStores', 
               'Gyms', 
               'Vintage&Consignment', 
               'Doctors', 
               'Waxing', 
               'Apartments', 
               'Tires', 
               'Education', 
               'Accessories', 
               'Trainers',
               'Contractors', 
               'Massage', 
               'Grocery', 
               'Automotive', 
               'ActiveLife', 
               'Fitness&Instruction', 
               'Orthodontists', 
               'JewelryRepair', 
               'Engraving', 
               'IntervalTrainingGyms', 
               'Dentists', 
               'Health&Medical', 
               'LocalServices', 
               'Home&Garden', 
               'Shopping', 
               'FurnitureStores', 
               'Gyms', 
               'Vintage&Consignment']

for i in remove_list:
    if i in cats_raw:
        del cats_raw[i]

In [79]:
state_cuisine = {}
for i in tqdm(states):  
    state_cuisine[i] = {}
    for k, v in cats_raw.items():
        state_cuisine[i][k] = business[(business['state'] == i) & (business['categories'].str.contains(k)==True)].shape[0]

  0%|          | 0/9 [00:00<?, ?it/s]/opt/anaconda3/lib/python3.8/site-packages/pandas/core/strings/accessor.py:101: UserWarning:

This pattern has match groups. To actually get the groups, use str.extract.

/opt/anaconda3/lib/python3.8/site-packages/pandas/core/strings/accessor.py:101: UserWarning:

This pattern has match groups. To actually get the groups, use str.extract.

/opt/anaconda3/lib/python3.8/site-packages/pandas/core/strings/accessor.py:101: UserWarning:

This pattern has match groups. To actually get the groups, use str.extract.

 11%|█         | 1/9 [00:11<01:35, 11.96s/it]/opt/anaconda3/lib/python3.8/site-packages/pandas/core/strings/accessor.py:101: UserWarning:

This pattern has match groups. To actually get the groups, use str.extract.

/opt/anaconda3/lib/python3.8/site-packages/pandas/core/strings/accessor.py:101: UserWarning:

This pattern has match groups. To actually get the groups, use str.extract.

/opt/anaconda3/lib/python3.8/site-packages/pandas/core/strings/

In [80]:
def take(n, iterable):
    return list(islice(iterable, n))

In [94]:
for i in states:
    state_cuisine[i] = dict(sorted(state_cuisine[i].items(), key=lambda item: item[1], reverse=True))
    
for i in states:
    print("Top cuisines in "+i+":")
    top = take(10, state_cuisine[i].items())
    for i in range(len(top)):
        print(top[i][0])
    print()

Top cuisines in MA:
Bars
Nightlife
Sandwiches
Pizza
Italian
Seafood
Chinese
Salad
Burgers
Cafes

Top cuisines in FL:
Bars
Nightlife
Sandwiches
Burgers
Pizza
Italian
Seafood
Mexican
Salad
Chinese

Top cuisines in OR:
Bars
Nightlife
Sandwiches
Mexican
Burgers
Pizza
Cafes
Japanese
Thai
Vegan

Top cuisines in BC:
Bars
Chinese
Japanese
Nightlife
Cafes
Sandwiches
Pizza
Burgers
Seafood
Italian

Top cuisines in GA:
Bars
Nightlife
Sandwiches
Burgers
Pizza
Mexican
Seafood
Salad
Southern
Italian

Top cuisines in TX:
Bars
Nightlife
Mexican
Sandwiches
Burgers
Pizza
Tex-Mex
Caterers
Italian
Barbeque

Top cuisines in OH:
Bars
Nightlife
Sandwiches
Pizza
Burgers
Salad
Mexican
Italian
Chinese
Seafood

Top cuisines in CO:
Bars
Nightlife
Sandwiches
Pizza
Mexican
Italian
Salad
Burgers
Delis
Cafes

Top cuisines in WA:
Bars
Nightlife
Sandwiches
Burgers
Mexican
Pizza
Chinese
Japanese
Cafes
Thai



In [95]:
print(states.keys())

dict_keys(['MA', 'FL', 'OR', 'BC', 'GA', 'TX', 'OH', 'CO', 'WA'])


In [98]:
user_state = input("Pick a state: ")
user_rest_type = input("Pick Restaurant type: ")
user_df = business[(business['state'] == user_state) & (business['categories'].str.contains(user_rest_type)==True)][['name', 'stars', 'city', 'latitude', 'longitude']]
user_df.reset_index(drop= True, inplace= True)
user_df

Pick a state: MA
Pick Restaurant type: Bar


name  stars     city   latitude  longitude
0                 Our Fathers    3.5  Allston  42.363543 -71.129559
1              Roppongi Sushi    2.5  Allston  42.350361 -71.131933
2          New Sushi and Poke    3.5  Allston  42.352416 -71.128550
3        Tavern in the Square    3.0  Allston  42.353307 -71.132638
4      Kirin Teppanyaki & Wok    3.5  Allston  42.352794 -71.131823
...                       ...    ...      ...        ...        ...
2256      Revolution Catering    5.0   Woburn  42.514896 -71.148706
2257            Tanner Tavern    3.0   Woburn  42.481899 -71.150955
2258           99 Restaurants    3.0   Woburn  42.502894 -71.134872
2259          Waxy O'Connor's    2.5   Woburn  42.480488 -71.118764
2260  Pintxo Pincho Tapas Bar    4.5   Woburn  42.479922 -71.151637

[2261 rows x 5 columns]

In [99]:
mapbox_access_token = 'pk.eyJ1IjoicHJhandhbGtob3QxNCIsImEiOiJja3d1NHQzeDkxbW9qMm5qdmVzaDloMWNhIn0.CFF-9llt4RnfRomF64MDcg'

fig = go.Figure()

fig.add_trace(go.Scattermapbox(
        lat=user_df['latitude'],
        lon=user_df['longitude'],
        mode='markers',
        marker=go.scattermapbox.Marker(
            size=10,
            color='rgb(255, 0, 0)',
            opacity=0.7
        ),
        text=user_df['name'],
        hoverinfo='text'
    ))

fig.update_layout(
    title=user_rest_type+" in "+user_state,
    autosize=True,
    hovermode='closest',
    showlegend=False,
    width=1000,
    height=600,
    mapbox=dict(
        accesstoken=mapbox_access_token,
        bearing=0,
        center=dict(
            lat=38,
            lon=-94
        ),
        pitch=0,
        zoom=3,
        style='light'
    ),
)

fig.show()


In [100]:
top_state = input("Pick a state: ")
top = take(10, state_cuisine[top_state].items())
print(top)
first_tuple_elements = [a_tuple[0] for a_tuple in top]
for i in range(len(first_tuple_elements)):
    globals()["df%s" %i] = business[(business['state'] == user_state) & (business['categories'].str.contains(first_tuple_elements[i])==True)][['name', 'stars', 'city', 'latitude', 'longitude']]
    globals()["df%s" %i]['category'] = first_tuple_elements[i]
    globals()["df%s" %i].reset_index(drop= True, inplace= True)
frames = [df0, df1, df2, df3, df4, df5, df6, df7, df8, df9]

Pick a state: MA
[('Bars', 2139), ('Nightlife', 1667), ('Sandwiches', 1655), ('Pizza', 1510), ('Italian', 1035), ('Seafood', 707), ('Chinese', 669), ('Salad', 630), ('Burgers', 618), ('Cafes', 565)]


In [86]:
df1

name  stars     city   latitude  longitude  \
0                           Big City    3.5  Allston  42.352750 -71.131717   
1                        Our Fathers    3.5  Allston  42.363543 -71.129559   
2               Tavern in the Square    3.0  Allston  42.353307 -71.132638   
3                       Sports Depot    3.0  Allston  42.356119 -71.132499   
4                 Lone Star Taco Bar    4.0  Allston  42.353849 -71.137078   
...                              ...    ...      ...        ...        ...   
1662                Sea Dog Brew Pub    2.5   Woburn  42.503081 -71.140437   
1663  black and orange bar and grill    3.5   Woburn  42.481925 -71.150932   
1664                   Tanner Tavern    3.0   Woburn  42.481899 -71.150955   
1665                  99 Restaurants    3.0   Woburn  42.502894 -71.134872   
1666                 Waxy O'Connor's    2.5   Woburn  42.480488 -71.118764   

       category  
0     Nightlife  
1     Nightlife  
2     Nightlife  
3     Nightlife  
4     Nightlife  
...         ...  
1662  Nightlife  
1663  Nightlife  
1664  Nightlife  
1665  Nightlife  
1666  Nightlife  

[1667 rows x 6 columns]

In [101]:
top_state = input("Pick a state: ")
top = take(10, state_cuisine[top_state].items())
print(top)
first_tuple_elements = [a_tuple[0] for a_tuple in top]
for i in range(len(first_tuple_elements)):
    globals()["df%s" %i] = business[(business['state'] == top_state) & (business['categories'].str.contains(first_tuple_elements[i])==True)][['name', 'stars', 'city', 'latitude', 'longitude']]
    globals()["df%s" %i]['category'] = first_tuple_elements[i]
    globals()["df%s" %i].reset_index(drop= True, inplace= True)
frames = [df0, df1, df2, df3, df4, df5, df6, df7, df8, df9]

mapbox_access_token = 'pk.eyJ1IjoicHJhandhbGtob3QxNCIsImEiOiJja3d1NHQzeDkxbW9qMm5qdmVzaDloMWNhIn0.CFF-9llt4RnfRomF64MDcg'

fig = go.Figure()

for i in frames:
    rgb = list(np.random.choice(range(256), size=3))
    r = rgb[0]
    g = rgb[1]
    b = rgb[2]
    fig.add_trace(go.Scattermapbox(
            lat=i['latitude'],
            lon=i['longitude'],
            mode='markers',
            marker=go.scattermapbox.Marker(
                size=10,
                color='rgb('+str(r)+','+str(g)+','+str(b)+')',
                opacity=0.7
            ),
            text=i['name'],
            hoverinfo='text',
            name= i.iloc[0, 5]
        ))

fig.update_layout(
    title=top_state,
    autosize=True,
    hovermode='closest',
    showlegend=True,
    width=1000,
    height=900,
    mapbox=dict(
        accesstoken=mapbox_access_token,
        bearing=0,
        center=dict(
            lat=38,
            lon=-94
        ),
        pitch=0,
        zoom=3,
        style='light'
    ),
)

fig.show()


Pick a state: FL
[('Bars', 1550), ('Nightlife', 1147), ('Sandwiches', 1065), ('Burgers', 772), ('Pizza', 765), ('Italian', 615), ('Seafood', 572), ('Mexican', 496), ('Salad', 457), ('Chinese', 381)]


#### Business part

In [143]:
busi_type = input("Enter the type Restaurant: ")
busi_state = input("State: ")
print("User would like to open "+busi_type+" in "+busi_state)
top = take(10, state_cuisine[busi_state].items())
t1 = top[:5]
t2 = top[5:]
flag = False
for i in t1:
    if busi_type in i[0]:
        print("This location is a great choice for "+busi_type+", but you will have quite a lot of competition.")
        flag = True
for i in t2:
    if busi_type in i[0]:
        print("There is a good business potential for "+busi_type+".")
        flag = True
if flag == False:
    print("We would suggest running some other type of restaurant.")
    print("Maybe you can consider the following:")
    for i in top:
        print("\t*",i[0])

Enter the type Restaurant: Indian
State: FL
User would like to open Indian in FL
We would suggest running some other type of restaurant.
Maybe you can consider the following:
	* Bars
	* Nightlife
	* Sandwiches
	* Burgers
	* Pizza
	* Italian
	* Seafood
	* Mexican
	* Salad
	* Chinese
